In [1]:
from pgtools.gff_parser import parse_GFFs_dir

In [2]:
simple_gffs = parse_GFFs_dir("/home/pampuch/studia/magisterka/GPSC_subset/gff")

In [3]:
for g, gff in simple_gffs.simple_GFFs.items():
    print(g)

17870_7_11.velvet
15841_4_38.velvet
19341_2_35.velvet
19084_7_49.velvet
21053_8_138.velvet
14520_5_48.velvet
23164_8_98.velvet
17870_7_77.velvet
22667_7_131.velvet
22841_3_20.velvet
17794_8_81.velvet
18090_1_123.velvet
22841_3_7.velvet
23164_8_137.velvet
15841_4_17.velvet
17870_7_102.velvet
17138_5_34.velvet
22841_3_158.velvet
22027_1_69.velvet
22027_1_155.velvet


In [4]:
gff = simple_gffs.simple_GFFs["17870_7_11.velvet"]

In [8]:
for scaff, coords in gff.scaffolds_coords.items():
    print(scaff,coords)

ERS725493_SC_contig000001 {<pgtools.gff_parser.SimpleAnnotation object at 0x7fbf399e0070>, <pgtools.gff_parser.SimpleAnnotation object at 0x7fbf399e8070>, <pgtools.gff_parser.SimpleAnnotation object at 0x7fbf399e00d0>, <pgtools.gff_parser.SimpleAnnotation object at 0x7fbf399e80d0>, <pgtools.gff_parser.SimpleAnnotation object at 0x7fbf399e0130>, <pgtools.gff_parser.SimpleAnnotation object at 0x7fbf399e8130>, <pgtools.gff_parser.SimpleAnnotation object at 0x7fbf399e0190>, <pgtools.gff_parser.SimpleAnnotation object at 0x7fbf399e8190>, <pgtools.gff_parser.SimpleAnnotation object at 0x7fbf399e01f0>, <pgtools.gff_parser.SimpleAnnotation object at 0x7fbf399e81f0>, <pgtools.gff_parser.SimpleAnnotation object at 0x7fbf399e0250>, <pgtools.gff_parser.SimpleAnnotation object at 0x7fbf399e8250>, <pgtools.gff_parser.SimpleAnnotation object at 0x7fbf399e02b0>, <pgtools.gff_parser.SimpleAnnotation object at 0x7fbf399e82b0>, <pgtools.gff_parser.SimpleAnnotation object at 0x7fbf399e0310>, <pgtools.gff_

In [10]:
scaff_cds = {scaff:{cds.annotation_id:[] for cds in coords} for scaff, coords in gff.scaffolds_coords.items()}

In [11]:
scaff_cds

{'ERS725493_SC_contig000001': {'17870_7#11_00137': [],
  '17870_7#11_00307': [],
  '17870_7#11_00138': [],
  '17870_7#11_00308': [],
  '17870_7#11_00139': [],
  '17870_7#11_00309': [],
  '17870_7#11_00140': [],
  '17870_7#11_00310': [],
  '17870_7#11_00141': [],
  '17870_7#11_00311': [],
  '17870_7#11_00142': [],
  '17870_7#11_00312': [],
  '17870_7#11_00143': [],
  '17870_7#11_00313': [],
  '17870_7#11_00144': [],
  '17870_7#11_00314': [],
  '17870_7#11_00145': [],
  '17870_7#11_00315': [],
  '17870_7#11_00146': [],
  '17870_7#11_00316': [],
  '17870_7#11_00147': [],
  '17870_7#11_00317': [],
  '17870_7#11_00148': [],
  '17870_7#11_00318': [],
  '17870_7#11_00149': [],
  '17870_7#11_00319': [],
  '17870_7#11_00150': [],
  '17870_7#11_00320': [],
  '17870_7#11_00151': [],
  '17870_7#11_00321': [],
  '17870_7#11_00152': [],
  '17870_7#11_00322': [],
  '17870_7#11_00153': [],
  '17870_7#11_00323': [],
  '17870_7#11_00154': [],
  '17870_7#11_00324': [],
  '17870_7#11_00155': [],
  '17870_

In [12]:
def intersection_len(s1_coords, s2_coords):
    """
    seq2 is assumed to be from MAF and seq1 from gfa (checking how well
    seq1 fits into seq2)
    """
    s1_start, s1_end = s1_coords
    s2_start, s2_end = s2_coords
    if s1_end < s2_start or s1_start > s2_end:
        return 0

    if s1_start < s2_start:
        inter_start = s2_start
    else:
        inter_start = s1_start    

    if s1_end > s2_end:
        inter_end = s2_end
    else:
        inter_end = s1_end
        
    return inter_end - inter_start + 1

In [ ]:
s = "0123456789"

In [ ]:
intersection_len((1,4),(2,8))

In [ ]:
intersection_len((2,8),(1,4))

In [ ]:
intersection_len((1,7),(3,5))

In [ ]:
intersection_len((3,5),(1,7))

In [ ]:
for scaff, coords in gff.items():
    for cds_coords in coords:
        s = cds_coords[0]
        e = cds_coords[1]
        ann_id = cds_coords[-1]
        for cds in coords:
            if intersection_len((s,e), (cds[0], cds[1])) > 0 and ann_id != cds[-1]:
                scaff_cds[scaff][ann_id].append((cds[-1], intersection_len((s,e), (cds[0], cds[1]))))
                

In [ ]:
scaff_cds

In [13]:
def get_overlaps_in_gff(gff):
    scaff_cds = {scaff:{cds.annotation_id:[] for cds in coords} for scaff, coords in gff.scaffolds_coords.items()}
    for scaff, coords in gff.scaffolds_coords.items():
        for cds_coords in coords:
            s = cds_coords.start
            e = cds_coords.end
            ann_id = cds_coords.annotation_id
            for cds in coords:
                if intersection_len((s,e), (cds.start, cds.end)) > 0 and ann_id != cds.annotation_id:
                    scaff_cds[scaff][ann_id].append((cds.annotation_id, intersection_len((s,e), (cds.start, cds.end))))
    return scaff_cds

def get_highest_overlap(gff):
    scaff_overlaps = get_overlaps_in_gff(gff)
    max_overlap = 0
    scaffold = None
    id_1 = None
    id_2 = None
    for scaff, cds in scaff_overlaps.items():
        for cds_, overlaps in cds.items():
            for el in overlaps:
                if el[-1] > max_overlap:
                    max_overlap = el[-1]
                    id_1 = cds_
                    id_2 = el[0]
                    scaffold = scaff
    return {"scaffold":scaffold, "cds_1":id_1, "cds_2":id_2, "overlap":max_overlap}
                    
    

In [14]:
get_highest_overlap(gff)

{'scaffold': 'ERS725493_SC_contig000005',
 'cds_1': '17870_7#11_01276',
 'cds_2': '17870_7#11_01277',
 'overlap': 381}

In [15]:
overlaps = {}
for genome, gff in simple_gffs.simple_GFFs.items():
    overlaps[genome] = get_highest_overlap(gff)

In [16]:
overlaps

{'17870_7_11.velvet': {'scaffold': 'ERS725493_SC_contig000005',
  'cds_1': '17870_7#11_01276',
  'cds_2': '17870_7#11_01277',
  'overlap': 381},
 '15841_4_38.velvet': {'scaffold': 'ERS639881_SC_contig000035',
  'cds_1': '15841_4#38_02076',
  'cds_2': '15841_4#38_02077',
  'overlap': 381},
 '19341_2_35.velvet': {'scaffold': 'ERS813179_SC_contig000006',
  'cds_1': '19341_2#35_01573',
  'cds_2': '19341_2#35_01574',
  'overlap': 381},
 '19084_7_49.velvet': {'scaffold': 'ERS1021351_SC_contig000001',
  'cds_1': '19084_7#49_00007',
  'cds_2': '19084_7#49_00008',
  'overlap': 381},
 '21053_8_138.velvet': {'scaffold': 'ERS1299630_SC_contig000002',
  'cds_1': '21053_8#138_00266',
  'cds_2': '21053_8#138_00267',
  'overlap': 381},
 '14520_5_48.velvet': {'scaffold': 'ERS525028_SC_contig000004',
  'cds_1': '14520_5#48_00799',
  'cds_2': '14520_5#48_00800',
  'overlap': 381},
 '23164_8_98.velvet': {'scaffold': '_SC_contig000007',
  'cds_1': '23164_8#98_01283',
  'cds_2': '23164_8#98_01284',
  'overl

In [18]:
klebsiella_dff = "/home/pampuch/studia/magisterka/test_data/klebsiella_subset_old/gff/"

In [19]:
simple_gffs = parse_GFFs_dir(klebsiella_dff)

In [22]:
overlaps = {}
for genome, gff in simple_gffs.simple_GFFs.items():
    overlaps[genome] = get_overlaps_in_gff(gff)

In [23]:
overlaps

{'5235_5_12': {'contig00001': {'KKAGLBML_00057': [],
   'KKAGLBML_00036': [],
   'KKAGLBML_00015': [('KKAGLBML_00014', 23)],
   'KKAGLBML_00058': [],
   'KKAGLBML_00037': [],
   'KKAGLBML_00016': [],
   'KKAGLBML_00059': [('KKAGLBML_00060', 4)],
   'KKAGLBML_00038': [],
   'KKAGLBML_00017': [],
   'KKAGLBML_00060': [('KKAGLBML_00059', 4)],
   'KKAGLBML_00039': [],
   'KKAGLBML_00018': [],
   'KKAGLBML_00061': [],
   'KKAGLBML_00040': [],
   'KKAGLBML_00019': [('KKAGLBML_00020', 14)],
   'KKAGLBML_00062': [],
   'KKAGLBML_00041': [],
   'KKAGLBML_00020': [('KKAGLBML_00019', 14), ('KKAGLBML_00021', 8)],
   'KKAGLBML_00042': [],
   'KKAGLBML_00021': [('KKAGLBML_00020', 8)],
   'KKAGLBML_00043': [],
   'KKAGLBML_00022': [],
   'KKAGLBML_00001': [],
   'KKAGLBML_00044': [],
   'KKAGLBML_00023': [],
   'KKAGLBML_00002': [],
   'KKAGLBML_00045': [],
   'KKAGLBML_00024': [],
   'KKAGLBML_00003': [('KKAGLBML_00004', 4)],
   'KKAGLBML_00046': [],
   'KKAGLBML_00025': [],
   'KKAGLBML_00004': [('

In [ ]:
overlaps

In [ ]:
simple_gffs.simple_GFFs


In [21]:
KB_all_overlaps = get_overlaps_in_gff(simple_gffs)

AttributeError: 'Pangenome_Gffs' object has no attribute 'scaffolds_coords'

In [ ]:
sequence_cds = {}

for genome, gff in simple_gffs.simple_GFFs.items():
    for scaff, cds_coords in gff.items():
        seq_name = f"{genome}.{scaff}"
        sequence_cds[seq_name] = []
        for coords in cds_coords:
            sequence_cds[seq_name].append(coords)

print(sequence_cds)

### Checking how many overlapping cds there are


In [ ]:
maf_dir = "/home/pampuch/studia/magisterka/test_data/klebsiella_subset_old/new_maf_mo_refound.maf"

In [ ]:
from pgtools.maf_parser import parse_maf

In [ ]:
maf = parse_maf(maf_dir)

In [ ]:
maf.coord_system

No refound, so all fragments should map

In [ ]:
# convert to gff coords system